# Datensatz Umstrukturierung für inhaltsbasiertes Empfehlungssystem

In [1]:
import pandas as pd
import re

ratings = pd.read_csv(r'ratings.csv',encoding='latin-1')
movies = pd.read_csv(r'movies.csv',encoding='latin-1')

## Schritt 1: Einschränken des Datensatzes

Der Datensatz beinhaltet 62 423 Filme. Da die Berechnungen für solche Datenmengen sehr lange dauern, schränken wir den Datensatz ein. Du kannst selbst anpassen, wie sehr du den Datensatz einschränken willst. 

In [9]:
movies_filter = movies[movies['movieId']<1000]
movies_filter

movieId                               title  \
0          1                    Toy Story (1995)   
1          2                      Jumanji (1995)   
2          3             Grumpier Old Men (1995)   
3          4            Waiting to Exhale (1995)   
4          5  Father of the Bride Part II (1995)   
..       ...                                 ...   
972      994                    Big Night (1996)   
973      996            Last Man Standing (1996)   
974      997                       Caught (1996)   
975      998                   Set It Off (1996)   
976      999         2 Days in the Valley (1996)   

                                          genres  
0    Adventure|Animation|Children|Comedy|Fantasy  
1                     Adventure|Children|Fantasy  
2                                 Comedy|Romance  
3                           Comedy|Drama|Romance  
4                                         Comedy  
..                                           ...  
972                                 Comedy|Drama  
973                  Action|Crime|Drama|Thriller  
974                               Drama|Thriller  
975                                 Action|Crime  
976                              Crime|Film-Noir  

[977 rows x 3 columns]

## Schritt 2: Aufspalten der Filminformationen

Aktuell stehen alle Genre in einer Spalte des DataFrames. Wir benötigen für jedes Genre eine einzelne Spalte, in welcher durch 0 oder 1 angegeben ist, ob ein Film das Genre beinhaltet oder nicht. Dafür erstellen wir für jedes Genre eine neue Spalte und betrachten, ob das Genre in den Genres des jeweiligen Films angegeben ist oder nicht.<br/><br/>

<i>Es kann sein, dass du eine Warnung erhälst, wenn du diesen Code ausführst. Diese kannst du ignoieren.</i>

In [10]:
for elem in movies_filter['genres'].str.split(pat = '|', expand = False).explode().unique():
    column = []
    for i in range(len(movies_filter)):
        if elem in movies_filter['genres'].str.split(pat = '|', expand = False)[i]:
            column.append(1)
        else:
            column.append(0)
    movies_filter[elem] = column
movies_filter

<ipython-input-10-80300bc5b093>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movies_filter[elem] = column


movieId                               title  \
0          1                    Toy Story (1995)   
1          2                      Jumanji (1995)   
2          3             Grumpier Old Men (1995)   
3          4            Waiting to Exhale (1995)   
4          5  Father of the Bride Part II (1995)   
..       ...                                 ...   
972      994                    Big Night (1996)   
973      996            Last Man Standing (1996)   
974      997                       Caught (1996)   
975      998                   Set It Off (1996)   
976      999         2 Days in the Valley (1996)   

                                          genres  Adventure  Animation  \
0    Adventure|Animation|Children|Comedy|Fantasy          1          1   
1                     Adventure|Children|Fantasy          1          0   
2                                 Comedy|Romance          0          0   
3                           Comedy|Drama|Romance          0          0   
4                                         Comedy          0          0   
..                                           ...        ...        ...   
972                                 Comedy|Drama          0          0   
973                  Action|Crime|Drama|Thriller          0          0   
974                               Drama|Thriller          0          0   
975                                 Action|Crime          0          0   
976                              Crime|Film-Noir          0          0   

     Children  Comedy  Fantasy  Romance  Drama  ...  Thriller  Horror  \
0           1       1        1        0      0  ...         0       0   
1           1       0        1        0      0  ...         0       0   
2           0       1        0        1      0  ...         0       0   
3           0       1        0        1      1  ...         0       0   
4           0       1        0        0      0  ...         0       0   
..        ...     ...      ...      ...    ...  ...       ...     ...   
972         0       1        0        0      1  ...         0       0   
973         0       0        0        0      1  ...         1       0   
974         0       0        0        0      1  ...         1       0   
975         0       0        0        0      0  ...         0       0   
976         0       0        0        0      0  ...         0       0   

     Mystery  Sci-Fi  IMAX  Documentary  War  Musical  Western  Film-Noir  
0          0       0     0            0    0        0        0          0  
1          0       0     0            0    0        0        0          0  
2          0       0     0            0    0        0        0          0  
3          0       0     0            0    0        0        0          0  
4          0       0     0            0    0        0        0          0  
..       ...     ...   ...          ...  ...      ...      ...        ...  
972        0       0     0            0    0        0        0          0  
973        0       0     0            0    0        0        0          0  
974        0       0     0            0    0        0        0          0  
975        0       0     0            0    0        0        0          0  
976        0       0     0            0    0        0        0          1  

[977 rows x 22 columns]

## Schritt 3: Spalten mit nicht notwendigen Informationen löschen

Unser inhaltsbasiertes Empfehlungssystem arbeitet nur mit den Informationen über die Genre der Filme. Daher löschen wir die Spalte mit dem Titel. Außerdem löschen wir die Genre Spalte, da diese Informationen nun in den anderen Spalten enthalten sind.<br/><br/>
<i>Achtung: Diese Codezelle kannst du nicht mehrmals ausführen, da die Spalten nicht nochmal gelöscht werden können.</i>

In [11]:
movies_filter = movies_filter.drop(['title','genres'], axis='columns')
movies_filter

movieId  Adventure  Animation  Children  Comedy  Fantasy  Romance  Drama  \
0          1          1          1         1       1        1        0      0   
1          2          1          0         1       0        1        0      0   
2          3          0          0         0       1        0        1      0   
3          4          0          0         0       1        0        1      1   
4          5          0          0         0       1        0        0      0   
..       ...        ...        ...       ...     ...      ...      ...    ...   
972      994          0          0         0       1        0        0      1   
973      996          0          0         0       0        0        0      1   
974      997          0          0         0       0        0        0      1   
975      998          0          0         0       0        0        0      0   
976      999          0          0         0       0        0        0      0   

     Action  Crime  Thriller  Horror  Mystery  Sci-Fi  IMAX  Documentary  War  \
0         0      0         0       0        0       0     0            0    0   
1         0      0         0       0        0       0     0            0    0   
2         0      0         0       0        0       0     0            0    0   
3         0      0         0       0        0       0     0            0    0   
4         0      0         0       0        0       0     0            0    0   
..      ...    ...       ...     ...      ...     ...   ...          ...  ...   
972       0      0         0       0        0       0     0            0    0   
973       1      1         1       0        0       0     0            0    0   
974       0      0         1       0        0       0     0            0    0   
975       1      1         0       0        0       0     0            0    0   
976       0      1         0       0        0       0     0            0    0   

     Musical  Western  Film-Noir  
0          0        0          0  
1          0        0          0  
2          0        0          0  
3          0        0          0  
4          0        0          0  
..       ...      ...        ...  
972        0        0          0  
973        0        0          0  
974        0        0          0  
975        0        0          0  
976        0        0          1  

[977 rows x 20 columns]

## Schritt 4: Verknüpfen mit den Bewertungsinformationen des Nutzers

Du kannst hier einen Nutzer auswählen, für den du die Tabelle ausgeben möchtest. Die Filminformationen werden dann mit den Bewertungsinformationen verknüpft. Mehr dazu findest du auf inf-schule 14.5.1.1.2.3. Wir löschen die Spalten der userId und des timesstamps, die beim Zusammenfügen hinzukommen, allerdings nicht für die inhaltsbasierten Empfehlungen benötigt werden.

In [14]:
nutzer = 2
ratings_user = ratings[ratings['userId']==nutzer]
total_user = pd.merge(movies_filter,ratings_user,left_on=['movieId'],
              right_on=['movieId'],
              how='inner').drop(['userId','timestamp'], axis='columns')
total_user

movieId  Adventure  Animation  Children  Comedy  Fantasy  Romance  Drama  \
0         1          1          1         1       1        1        0      0   
1        62          0          0         0       0        0        0      1   
2       110          0          0         0       0        0        0      1   
3       150          1          0         0       0        0        0      1   
4       151          0          0         0       0        0        1      1   
5       236          0          0         0       1        0        1      0   
6       260          1          0         0       0        0        0      0   
7       261          0          0         0       0        0        0      1   
8       266          0          0         0       0        0        1      1   
9       318          0          0         0       0        0        0      1   
10      333          0          0         0       1        0        0      0   
11      349          0          0         0       0        0        0      1   
12      356          0          0         0       1        0        1      1   
13      364          1          1         1       0        0        0      1   
14      380          1          0         0       1        0        1      0   
15      457          0          0         0       0        0        0      0   
16      480          1          0         0       0        0        0      0   
17      497          0          0         0       1        0        1      0   
18      524          0          0         0       0        0        0      1   
19      527          0          0         0       0        0        0      1   
20      534          0          0         0       0        0        1      1   
21      553          0          0         0       0        0        0      1   
22      588          1          1         1       1        0        0      0   
23      589          0          0         0       0        0        0      0   
24      653          1          0         0       0        1        0      0   
25      733          1          0         0       0        0        0      0   
26      858          0          0         0       0        0        0      1   
27      914          0          0         0       1        0        1      1   
28      953          0          0         1       0        1        1      1   

    Action  Crime  ...  Horror  Mystery  Sci-Fi  IMAX  Documentary  War  \
0        0      0  ...       0        0       0     0            0    0   
1        0      0  ...       0        0       0     0            0    0   
2        1      0  ...       0        0       0     0            0    1   
3        0      0  ...       0        0       0     1            0    0   
4        1      0  ...       0        0       0     0            0    1   
5        1      0  ...       0        0       0     0            0    0   
6        1      0  ...       0        0       1     0            0    0   
7        0      0  ...       0        0       0     0            0    0   
8        0      0  ...       0        0       0     0            0    1   
9        0      1  ...       0        0       0     0            0    0   
10       0      0  ...       0        0       0     0            0    0   
11       1      1  ...       0        0       0     0            0    0   
12       0      0  ...       0        0       0     0            0    1   
13       0      0  ...       0        0       0     1            0    0   
14       1      0  ...       0        0       0     0            0    0   
15       0      0  ...       0        0       0     0            0    0   
16       1      0  ...       0        0       1     0            0    0   
17       0      0  ...       0        0       0     0            0    0   
18       0      0  ...       0        0       0     0            0    0   
19       0      0  ...       0        0       0     0            0    1   
20       0      0  ...      